# Auswertung der Kommunalwahlergebnisse 2021 in Celle

In [1]:
import lxml.html as ht
import lxml.etree as et

In [2]:
from urllib.request import urlopen
from urllib.parse import urljoin

## Herunterladen der Daten

In [3]:
url = "https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/index.html"

In [4]:
with urlopen(url) as f:
    p = ht.parse(f)

In [5]:
gebiete = p.xpath('//div[h3 = "Untergeordnete Gebiete"]//ul//a')

In [6]:
[el.text for el in gebiete]

['Blumlage/Altstadt',
 'Altencelle',
 'Westercelle',
 'Neuenhäusen',
 'Wietzenbruch',
 'Neustadt/ Heese',
 'Klein Hehlen',
 'Boye',
 'Groß Hehlen gem. mit Scheuen und Hustedt',
 'Garßen',
 'Vorwerk',
 'Altenhagen gem. mit Bostel und Lachtehausen',
 'Hehlentor']

In [7]:
def parse_page(path, url, gesehen):
    if url in gesehen:
        return
    gesehen.add(url)

    print(', '.join(path), url)
    with urlopen(url) as f:
        page = ht.parse(f)

    gebiete = page.xpath('//div[h3 = "Untergeordnete Gebiete"]//ul//a')
    for gebiet in gebiete:
        yield from parse_page(path + [gebiet.text.strip()], urljoin(url, gebiet.get('href')), gesehen)

    stimmen = page.xpath('//table[contains(@class, "table-stimmen")]//tr[td[normalize-space()]]')
    data = [
        [(tr.findtext('th//abbr') or tr.findtext('th')).strip(), 1 if tr.findtext('th//abbr') else 0, tr.find('td[1]').get("data-sort"), tr.find('td[2]').get("data-sort")]
        for tr in stimmen
        if tr.findtext('th') != "Partei"
    ]
    if data:
        yield ['|'.join(path), data]

In [8]:
gesehen = set()
d = list(parse_page([], url, gesehen))

 https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/index.html
Blumlage/Altstadt https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_ortschaft_0601.html
Blumlage/Altstadt, Mehr-Generationen-Haus https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060101.html
Blumlage/Altstadt, Stadtbibliothek https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060102.html
Blumlage/Altstadt, Neues Rathaus / Alte Exerzierhalle (re) https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060103.html
Blumlage/Altstadt, Neues Rathaus / Alte Exerzierhalle (li) https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060104.html
Blumlage/Altstadt, IGS Celle https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060105.html
Blumlage/Altstadt, IGS Celle https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060106.html
Blumlage/Altstadt, DRK Kita https://wahl.landkreis-celle.de/

Boye https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_ortschaft_0608.html
Boye, Schießstand Boye https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060835.html
Boye, 121 Briefwahl Boye https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_briefwahlbezirk_351006061212.html
Groß Hehlen gem. mit Scheuen und Hustedt https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_ortschaft_0609.html
Groß Hehlen gem. mit Scheuen und Hustedt, GS Scheuen https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060936.html
Groß Hehlen gem. mit Scheuen und Hustedt, DGH Hustedt https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060937.html
Groß Hehlen gem. mit Scheuen und Hustedt, Kita Groß Hehlen https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbezirk_060938.html
Groß Hehlen gem. mit Scheuen und Hustedt, Haus der Vereine https://wahl.landkreis-celle.de/ivu/ortsrat2021_cel/ergebnisse_stimmbe

In [9]:
len(d)

105

In [10]:
d

[['Blumlage/Altstadt|Mehr-Generationen-Haus',
  [['CDU', 1, '108', '20.1869158879'],
   ['SPD', 1, '143', '26.7289719626'],
   ['AfD', 1, '41', '7.6635514019'],
   ['Die Grünen', 1, '124', '23.1775700935'],
   ['FDP', 1, '65', '12.1495327103'],
   ['Die UNABHÄNGIGEN', 1, '42', '7.8504672897'],
   ['Zukunft Celle', 1, '12', '2.2429906542'],
   ['Stimmberechtigte', 0, '567', ''],
   ['Wähler', 0, '183', ''],
   ['Ungültige Stimmzettel', 0, '2', '1.0928961749'],
   ['Gültige Stimmen', 0, '535', '']]],
 ['Blumlage/Altstadt|Stadtbibliothek',
  [['CDU', 1, '114', '21.5500945180'],
   ['SPD', 1, '91', '17.2022684310'],
   ['AfD', 1, '33', '6.2381852552'],
   ['Die Grünen', 1, '176', '33.2703213611'],
   ['FDP', 1, '59', '11.1531190926'],
   ['Die UNABHÄNGIGEN', 1, '42', '7.9395085066'],
   ['Zukunft Celle', 1, '14', '2.6465028355'],
   ['Stimmberechtigte', 0, '602', ''],
   ['Wähler', 0, '184', ''],
   ['Ungültige Stimmzettel', 0, '5', '2.7173913043'],
   ['Gültige Stimmen', 0, '529', '']]],


In [11]:
import json
with open("Celle_2021.json", "w", encoding="utf-8") as f:
    json.dump(d, f)

In [12]:
with open("Celle_2021.csv", "w", encoding='utf-8') as f:
    f.write("Stadtteil\tWahlbereich\tGruppe\tistPartei\tStimmen\tProzent\n")
    for gebiete, stimmen in d:
        gebiete = (gebiete.split("|") + [''])[:2]
        for partei, ist_partei, stimme, prozent in stimmen:
            f.write(f"{gebiete[0]}\t{gebiete[1]}\t{partei}\t{ist_partei}\t{stimme}\t{prozent}\n")

## Auswertung der Daten

Ab hier sind alle Daten lokal geschrieben und die Ausführung kann beliebig oft wiederholt werden.

In [72]:
with open("Celle_2021.json", "r", encoding="utf-8") as f:
    data = json.load(f)

In [161]:
flat_data_all = [
    (ort.replace(' (re)', '').replace(' (li)', ''), ist_partei, partei, int(stimmen) if stimmen else 0, float(prozent) if prozent else 0)
    for (ort, abstimmung) in data
    for (partei, ist_partei, stimmen, prozent) in abstimmung
]

In [162]:
flat_data_all

[('Blumlage/Altstadt|Mehr-Generationen-Haus', 1, 'CDU', 108, 20.1869158879),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus', 1, 'SPD', 143, 26.7289719626),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus', 1, 'AfD', 41, 7.6635514019),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus',
  1,
  'Die Grünen',
  124,
  23.1775700935),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus', 1, 'FDP', 65, 12.1495327103),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus',
  1,
  'Die UNABHÄNGIGEN',
  42,
  7.8504672897),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus',
  1,
  'Zukunft Celle',
  12,
  2.2429906542),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus', 0, 'Stimmberechtigte', 567, 0),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus', 0, 'Wähler', 183, 0),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus',
  0,
  'Ungültige Stimmzettel',
  2,
  1.0928961749),
 ('Blumlage/Altstadt|Mehr-Generationen-Haus', 0, 'Gültige Stimmen', 535, 0),
 ('Blumlage/Altstadt|Stadtbibliothek', 1, 'CDU', 114, 21.550094518),
 ('Blumlage/Altstadt|S

Es scheint sinnvoll, getrennte Wahlzimmer eines Wahlortes zusammenzufassen.

In [163]:
from itertools import groupby
from operator import itemgetter

In [164]:
def sums(items):
    suma = sumb = 0
    for *_, stimmen, prozent in items:
        suma += stimmen
        sumb += stimmen / (prozent / 100) if prozent else 0
    return (suma, 100 * suma / sumb if sumb else 0)

flat_data_agg = [
    (ort, ist_partei, partei) + sums(items)
    for (ort, ist_partei, partei), items in groupby(sorted(flat_data_all), key=itemgetter(0, 1, 2))
]

In [165]:
flat_data_agg[:10]

[('Altencelle', 0, 'Gültige Stimmen', 5791, 0),
 ('Altencelle', 0, 'Stimmberechtigte', 3878, 0),
 ('Altencelle', 0, 'Ungültige Stimmzettel', 57, 2.7818448022999998),
 ('Altencelle', 0, 'Wähler', 2049, 0),
 ('Altencelle', 1, 'AfD', 400, 6.9072699016),
 ('Altencelle', 1, 'CDU', 2245, 38.7670523226),
 ('Altencelle', 1, 'Die Grünen', 587, 10.1364185806),
 ('Altencelle', 1, 'Die UNABHÄNGIGEN', 318, 5.4912795717),
 ('Altencelle', 1, 'FDP', 416, 7.1835606976),
 ('Altencelle', 1, 'SPD', 1687, 29.131410809899997)]

In [166]:
flat_data = [(ort, partei, stimmen, prozent) for (ort, ist_partei, partei, stimmen, prozent) in flat_data_agg if ist_partei]

In [167]:
nach_prozent = sorted(flat_data, key=itemgetter(3), reverse=True)

In [168]:
nach_prozent

[('Boye|121 Briefwahl Boye', 'CDU', 374, 69.00369003690001),
 ('Boye', 'CDU', 959, 68.4511063526),
 ('Boye|Schießstand Boye', 'CDU', 585, 68.1024447031),
 ('Klein Hehlen|Dietrich-Bonhoeffer-Haus', 'CDU', 982, 53.956043956038066),
 ('Klein Hehlen|120 Briefwahl', 'CDU', 582, 52.4324324324),
 ('Groß Hehlen gem. mit Scheuen und Hustedt|Kita Groß Hehlen',
  'CDU',
  456,
  51.700680272099994),
 ('Garßen|124 Briefwahl', 'CDU', 564, 48.453608247400005),
 ('Altenhagen gem. mit Bostel und Lachtehausen|BBS I',
  'CDU',
  776,
  47.317073170733124),
 ('Garßen', 'CDU', 1857, 46.5530208072),
 ('Altencelle|105 Briefwahl', 'CDU', 483, 46.1759082218),
 ('Garßen|GS Garßen', 'CDU', 1293, 45.769911504430084),
 ('Klein Hehlen', 'CDU', 3788, 45.4469106179),
 ('Klein Hehlen|121 Briefwahl Klein Hehlen', 'CDU', 405, 45.1002227171),
 ('Altenhagen gem. mit Bostel und Lachtehausen', 'CDU', 1560, 44.5205479452),
 ('Groß Hehlen gem. mit Scheuen und Hustedt|122 Briefwahl',
  'CDU',
  457,
  43.690248566),
 ('Groß H

### Höchste Prozentzahl

In [169]:
for gebiet, partei, stimmen, prozent in sorted(flat_data, key=itemgetter(3), reverse=True)[:40]:
    print(f"{partei:30s}  {prozent:3.1f}%  {stimmen:5d}   {gebiet}")

CDU                             69.0%    374   Boye|121 Briefwahl Boye
CDU                             68.5%    959   Boye
CDU                             68.1%    585   Boye|Schießstand Boye
CDU                             54.0%    982   Klein Hehlen|Dietrich-Bonhoeffer-Haus
CDU                             52.4%    582   Klein Hehlen|120 Briefwahl
CDU                             51.7%    456   Groß Hehlen gem. mit Scheuen und Hustedt|Kita Groß Hehlen
CDU                             48.5%    564   Garßen|124 Briefwahl
CDU                             47.3%    776   Altenhagen gem. mit Bostel und Lachtehausen|BBS I
CDU                             46.6%   1857   Garßen
CDU                             46.2%    483   Altencelle|105 Briefwahl
CDU                             45.8%   1293   Garßen|GS Garßen
CDU                             45.4%   3788   Klein Hehlen
CDU                             45.1%    405   Klein Hehlen|121 Briefwahl Klein Hehlen
CDU                             44.5%   15

In [170]:
for gebiet, partei, stimmen, prozent in sorted((row for row in flat_data if '|' in row[0]), key=itemgetter(3), reverse=True)[:40]:
    print(f"{partei:30s}  {prozent:3.1f}%  {stimmen:5d}   {gebiet}")

CDU                             69.0%    374   Boye|121 Briefwahl Boye
CDU                             68.1%    585   Boye|Schießstand Boye
CDU                             54.0%    982   Klein Hehlen|Dietrich-Bonhoeffer-Haus
CDU                             52.4%    582   Klein Hehlen|120 Briefwahl
CDU                             51.7%    456   Groß Hehlen gem. mit Scheuen und Hustedt|Kita Groß Hehlen
CDU                             48.5%    564   Garßen|124 Briefwahl
CDU                             47.3%    776   Altenhagen gem. mit Bostel und Lachtehausen|BBS I
CDU                             46.2%    483   Altencelle|105 Briefwahl
CDU                             45.8%   1293   Garßen|GS Garßen
CDU                             45.1%    405   Klein Hehlen|121 Briefwahl Klein Hehlen
CDU                             43.7%    457   Groß Hehlen gem. mit Scheuen und Hustedt|122 Briefwahl
CDU                             43.2%    341   Groß Hehlen gem. mit Scheuen und Hustedt|123 Briefwahl
CDU 

### Höchste Stimmenzahl

In [171]:
for gebiet, partei, stimmen, prozent in sorted(flat_data, key=itemgetter(2), reverse=True)[:40]:
    print(f"{partei:30s}  {stimmen:5d}  {prozent:5.1f}%   {gebiet}")

CDU                              3788   45.4%   Klein Hehlen
CDU                              3092   32.4%   Hehlentor
CDU                              2816   32.7%   Neuenhäusen
CDU                              2779   31.5%   Westercelle
SPD                              2624   31.4%   Neustadt/ Heese
SPD                              2568   28.9%   Blumlage/Altstadt
SPD                              2514   28.5%   Westercelle
SPD                              2474   25.9%   Hehlentor
CDU                              2462   39.8%   Groß Hehlen gem. mit Scheuen und Hustedt
CDU                              2245   38.8%   Altencelle
CDU                              2228   25.0%   Blumlage/Altstadt
CDU                              1908   22.8%   Neustadt/ Heese
CDU                              1857   46.6%   Garßen
SPD                              1850   33.7%   Wietzenbruch
Die Grünen                       1832   19.2%   Hehlentor
SPD                              1805   29.2%   Groß Hehlen g

### Beste Ergebnisse der Parteien

In [172]:
from itertools import groupby

In [173]:
def beste(data, sort_key, group_key, count=3):
    for _, ergebnisse in groupby(sorted(data, key=sort_key, reverse=True), key=group_key):
        for i in range(count):
            gebiet, partei, stimmen, prozent = next(ergebnisse)
            print(f"{partei:30s}  {stimmen:5d}  {prozent:5.1f}%   {gebiet}")

In [174]:
sort_key = itemgetter(1, 3)  # (partei, prozent)
group_key = itemgetter(1)    # partei
count = 3

beste(flat_data, sort_key, group_key, count)

dieBasis LV Niedersachsen          35    4.0%   Groß Hehlen gem. mit Scheuen und Hustedt|Kita Groß Hehlen
dieBasis LV Niedersachsen          31    3.0%   Groß Hehlen gem. mit Scheuen und Hustedt|122 Briefwahl
dieBasis LV Niedersachsen          22    2.9%   Groß Hehlen gem. mit Scheuen und Hustedt|Haus der Vereine
Zukunft Celle                      79   14.6%   Boye|121 Briefwahl Boye
Zukunft Celle                     203   14.5%   Boye
Zukunft Celle                     124   14.4%   Boye|Schießstand Boye
WG                                113   10.9%   Westercelle|109 Briefwahl
WG                                 55    7.8%   Neustadt/ Heese|115 Briefwahl
WG                                135    7.0%   Neustadt/ Heese|GS Heese-Süd
SPD                               383   39.3%   Groß Hehlen gem. mit Scheuen und Hustedt|GS Scheuen
SPD                               197   39.3%   Wietzenbruch|114 Briefwahl
SPD                               276   39.0%   Altenhagen gem. mit Bostel und Lachteh

In [175]:
sort_key = itemgetter(1, 2)  # (partei, stimmen)
group_key = itemgetter(1)    # partei
count = 3

beste(flat_data, sort_key, group_key, count)

dieBasis LV Niedersachsen         154    2.5%   Groß Hehlen gem. mit Scheuen und Hustedt
dieBasis LV Niedersachsen          35    4.0%   Groß Hehlen gem. mit Scheuen und Hustedt|Kita Groß Hehlen
dieBasis LV Niedersachsen          31    3.0%   Groß Hehlen gem. mit Scheuen und Hustedt|122 Briefwahl
Zukunft Celle                     458    5.3%   Neuenhäusen
Zukunft Celle                     256    3.1%   Neustadt/ Heese
Zukunft Celle                     209    2.4%   Westercelle
WG                                538    6.1%   Westercelle
WG                                502    6.0%   Neustadt/ Heese
WG                                348    4.2%   Klein Hehlen
SPD                              2624   31.4%   Neustadt/ Heese
SPD                              2568   28.9%   Blumlage/Altstadt
SPD                              2514   28.5%   Westercelle
FDP                               673    7.6%   Blumlage/Altstadt
FDP                               632    6.6%   Hehlentor
FDP                

## Größe der Wahlbereiche

In [176]:
beteiligte = [
    (ort, {was: int(anzahl) for (_, ist_partei, was, anzahl, _) in zahlen if not ist_partei})
    for ort, zahlen in groupby(flat_data_agg, key=itemgetter(0))
]

In [177]:
beteiligte[:3]

[('Altencelle',
  {'Gültige Stimmen': 5791,
   'Stimmberechtigte': 3878,
   'Ungültige Stimmzettel': 57,
   'Wähler': 2049}),
 ('Altencelle|105 Briefwahl',
  {'Gültige Stimmen': 1046,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 8,
   'Wähler': 366}),
 ('Altencelle|106 Briefwahl',
  {'Gültige Stimmen': 885,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 10,
   'Wähler': 315})]

In [178]:
sorted([(ort, anzahl) for (ort, anzahl) in beteiligte if 'Brief' in ort], key=lambda x: x[1]['Wähler'], reverse=True)

[('Hehlentor|128 Briefwahl',
  {'Gültige Stimmen': 1441,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 16,
   'Wähler': 503}),
 ('Hehlentor|129 Briefwahl',
  {'Gültige Stimmen': 1318,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 16,
   'Wähler': 457}),
 ('Altenhagen gem. mit Bostel und Lachtehausen|126 Briefwahl',
  {'Gültige Stimmen': 1157,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 7,
   'Wähler': 397}),
 ('Garßen|124 Briefwahl',
  {'Gültige Stimmen': 1164,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 6,
   'Wähler': 397}),
 ('Klein Hehlen|120 Briefwahl',
  {'Gültige Stimmen': 1110,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 6,
   'Wähler': 388}),
 ('Neuenhäusen|112 Briefwahl',
  {'Gültige Stimmen': 1125,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 3,
   'Wähler': 383}),
 ('Neuenhäusen|111 Briefwahl',
  {'Gültige Stimmen': 990,
   'Stimmberechtigte': 0,
   'Ungültige Stimmzettel': 10,
   'Wähler': 370}),
 ('Altencelle|105 Brie

In [179]:
wahlbeteiligung = [
    (ort, anzahl['Wähler'] / anzahl['Stimmberechtigte'])
    for ort, anzahl in beteiligte
    if '|' not in ort
]

In [180]:
sorted(wahlbeteiligung, key=itemgetter(1), reverse=True)

[('Boye', 0.7128279883381924),
 ('Altenhagen gem. mit Bostel und Lachtehausen', 0.6994186046511628),
 ('Garßen', 0.6042850896370792),
 ('Groß Hehlen gem. mit Scheuen und Hustedt', 0.6013661202185793),
 ('Klein Hehlen', 0.5898932957519629),
 ('Westercelle', 0.5693788594260807),
 ('Hehlentor', 0.5587597932988831),
 ('Altencelle', 0.5283651366683858),
 ('Neuenhäusen', 0.5184741703729046),
 ('Wietzenbruch', 0.5057712486883525),
 ('Blumlage/Altstadt', 0.47088912291259216),
 ('Vorwerk', 0.43977591036414565),
 ('Neustadt/ Heese', 0.3775433308214017)]

In [181]:
berechtigte = [
    (ort, anzahl['Stimmberechtigte'])
    for ort, anzahl in beteiligte
    if '|' not in ort
]

In [182]:
sorted(berechtigte, key=itemgetter(1), reverse=True)

[('Neustadt/ Heese', 7962),
 ('Blumlage/Altstadt', 6647),
 ('Hehlentor', 5999),
 ('Neuenhäusen', 5846),
 ('Westercelle', 5506),
 ('Klein Hehlen', 4967),
 ('Altencelle', 3878),
 ('Wietzenbruch', 3812),
 ('Groß Hehlen gem. mit Scheuen und Hustedt', 3660),
 ('Garßen', 2287),
 ('Vorwerk', 2142),
 ('Altenhagen gem. mit Bostel und Lachtehausen', 1720),
 ('Boye', 686)]

In [183]:
nichtwähler = [
    (ort, anzahl['Stimmberechtigte'] - anzahl['Wähler'])
    for ort, anzahl in beteiligte
    if '|' not in ort
]

In [184]:
sorted(nichtwähler, key=itemgetter(1), reverse=True)

[('Neustadt/ Heese', 4956),
 ('Blumlage/Altstadt', 3517),
 ('Neuenhäusen', 2815),
 ('Hehlentor', 2647),
 ('Westercelle', 2371),
 ('Klein Hehlen', 2037),
 ('Wietzenbruch', 1884),
 ('Altencelle', 1829),
 ('Groß Hehlen gem. mit Scheuen und Hustedt', 1459),
 ('Vorwerk', 1200),
 ('Garßen', 905),
 ('Altenhagen gem. mit Bostel und Lachtehausen', 517),
 ('Boye', 197)]

Wo sind die Nichtwähler?

In [199]:
nichtwähler_wo = sorted([
    (ort, anzahl['Stimmberechtigte'] - anzahl['Wähler'], anzahl['Stimmberechtigte'], 1 - anzahl['Wähler'] / anzahl['Stimmberechtigte'])
    for ort, anzahl in beteiligte
    if anzahl['Stimmberechtigte']
], key=itemgetter(1), reverse=True)

for ort, anzahl, gesamt, prozent in nichtwähler_wo:
    print(f"{anzahl:4d} von {gesamt:4d} in {ort}  ({prozent * 100:.0f}%)")

4956 von 7962 in Neustadt/ Heese  (62%)
3517 von 6647 in Blumlage/Altstadt  (53%)
2815 von 5846 in Neuenhäusen  (48%)
2647 von 5999 in Hehlentor  (44%)
2421 von 3812 in Wietzenbruch|GS Wietzenbruch  (64%)
2371 von 5506 in Westercelle  (43%)
2108 von 2871 in Neustadt/ Heese|Hölty-Gymnasium  (73%)
2037 von 4967 in Klein Hehlen  (41%)
2035 von 2679 in Blumlage/Altstadt|Neues Rathaus / Alte Exerzierhalle  (76%)
1921 von 3004 in Westercelle|GS Bruchhagen  (64%)
1884 von 3812 in Wietzenbruch  (49%)
1829 von 3878 in Altencelle  (47%)
1768 von 2465 in Neustadt/ Heese|GS Heese-Süd  (72%)
1743 von 2667 in Altencelle|GS Altencelle  (65%)
1459 von 3660 in Groß Hehlen gem. mit Scheuen und Hustedt  (40%)
1437 von 2142 in Vorwerk|GS Vorwerk  (67%)
1426 von 2448 in Klein Hehlen|GS Klein Hehlen  (58%)
1357 von 2142 in Neuenhäusen|GS Waldweg  (63%)
1302 von 2287 in Garßen|GS Garßen  (57%)
1229 von 1700 in Neuenhäusen|Gesamtschule Celle, Aussenst. Bahnhofstraße  (72%)
1200 von 2142 in Vorwerk  (56%)
1179